In [1]:
import torch
import schnetpack as spk
import math
from schnetpack.datasets import QM9


import numpy as np
from numpy import savetxt

# Define Important Functions

In [2]:
def print_molecule(props):
    
    # load x,y,z coordinates tensors
    x = props['_positions'][ :,0]
    y = props['_positions'][ :,1]
    z = props['_positions'][ :,2]
    x = x.numpy()
    y = y.numpy()
    z = z.numpy()
    
    for i in range(len(z)):
        if props['_atomic_numbers'][i] == 1:
            print('H',x[i],y[i],z[i])
        if props['_atomic_numbers'][i] == 6:
            print('C',x[i],y[i],z[i])
        if props['_atomic_numbers'][i] == 7:
            print('N',x[i],y[i],z[i])     
        if props['_atomic_numbers'][i] == 8:
            print('O',x[i],y[i],z[i])
        if props['_atomic_numbers'][i] == 9:
            print('F',x[i],y[i],z[i]) 
    print('')  
    return x,y,z

def hook_v0(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global v0
    #Update the embedding_output variable to be equal to our output tensor
    v0=out_tensor 

def hook_v1(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global v1
    #Update the embedding_output variable to be equal to our output tensor
    v1=out_tensor 

def hook_v2(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global v2
    #Update the embedding_output variable to be equal to our output tensor
    v2=out_tensor  
    
def hook_emb(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global emb
    #Update the embedding_output variable to be equal to our output tensor
    emb=out_tensor 
#def convert_2D(number_of_atoms,rep):
#    layer = np.zeros((number_of_atoms,30))
#    for i in range(number_of_atoms):
#        for j in range(30):
#            layer[i][j] = rep[0][i][j]
#    return layer



In [4]:
qm9data = QM9('./qm9.db', download=True, remove_uncharacterized=True)
checkpoint_path = '../../../../data/trained_models/qm9_i3_30f_10000_5000/trained.pth'
split_file='../../../../data/trained_models/qm9_i3_30f_10000_5000/split.npz'
number_of_inputs = 5000

# Load split file 
train, val, test = spk.data.train_test_split(qm9data,split_file=split_file)

# Load atom ref data 
atomrefs = qm9data.get_atomref(QM9.U0)
print('U0 of hyrogen:', '{:.2f}'.format(atomrefs[QM9.U0][1][0]), 'eV')
print('U0 of carbon:', '{:.2f}'.format(atomrefs[QM9.U0][6][0]), 'eV')
print('U0 of oxygen:', '{:.2f}'.format(atomrefs[QM9.U0][8][0]), 'eV')
print('U0 of oxygen:', '{:.2f}'.format(atomrefs[QM9.U0][7][0]), 'eV')   

# Define SchNet representation model

schnet = spk.representation.SchNet(
    n_atom_basis=30, n_filters=30, n_gaussians=20, n_interactions=3,
    cutoff=4. , cutoff_network=spk.nn.cutoff.CosineCutoff
)

# Define SchNet output model and property to be predicted

output_U0 = spk.atomistic.Atomwise(n_in=30, atomref=atomrefs[QM9.U0])

# Define atomistic model

model = spk.AtomisticModel(representation=schnet,output_modules=output_U0)

# Load saved checkpoint file
load_checkpoint = torch.load(checkpoint_path)

#qm9_i6_30f_20g-1000-500-4_300.pth
# load model's state dictionary from saved checkpoint
model.load_state_dict(load_checkpoint)

#set up device for forward pass
device='cpu'

# load atoms converter 
converter = spk.data.AtomsConverter(device=device)

datao = np.zeros((1,30))
datahae = np.zeros((1))
dataoae = np.zeros((1))
datah = np.zeros((1,30))
data = np.zeros((1))
for idx in range(number_of_inputs):

    # load data for molecule
    at, props = qm9data.get_properties(idx)

    
    # print molecule for identification
    print(idx)
    x, y, z = print_molecule(props)
    number_of_atoms=len(z)

    # convert qm9 data to machine-readable form
    inputs = converter(at)

    #Instatiate layer output
    v0=None
    v1=None
    v2=None
    x=None       

    # Forward hook the model's interaction layer 
    model.representation.interactions[0].register_forward_hook(hook_v0)

    # Forward hook the model's interaction layer 
    model.representation.interactions[1].register_forward_hook(hook_v1)

    # Forward hook the model's interaction layer 
    model.representation.interactions[2].register_forward_hook(hook_v2)

    # Forward hook the model's interaction layer 
    model.representation.embedding.register_forward_hook(hook_emb)

    # Forward pass molecules through the model
    model(inputs)


    rep = emb + v0 + v1 + v2
    rows = np.zeros((number_of_atoms,30))
    for i in range(number_of_atoms):
        for j in range(30):
            rows[i][j] = rep[0][i][j]

    from schnetpack.atomistic.output_modules import yi

    yi=yi.detach().numpy()

    #save the vector of every oxygen atom encountered
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 8:
            datao = np.vstack((datao,rows[i]))
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 1:
            datah = np.vstack((datah,rows[i]))    
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 1:
            datahae = np.vstack((datahae,yi[0][i]))
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 8:
            dataoae = np.vstack((dataoae,yi[0][i]))
            

    x = props['_positions'][ :,0]
    y = props['_positions'][ :,1]
    z = props['_positions'][ :,2] 
    
    distance = np.zeros((number_of_atoms))
    dist_x = np.zeros((number_of_atoms))
    dist_y = np.zeros((number_of_atoms))    
    dist_z = np.zeros((number_of_atoms))

    #calculate E distance, to figure out neighbor
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 1:
            for j in range(number_of_atoms):
                dist_x[j] = x[i] - x[j]
                dist_y[j] = y[i] - y[j]
                dist_z[j] = z[i] - z[j]
                distance[j] = math.sqrt(dist_x[j]**2 + dist_y[j]**2 + dist_z[j]**2)
            
            neighbor_dist = distance[0]                    
            neighbor = 0
            for k in range(number_of_atoms):
                if distance[k] < neighbor_dist and distance[k] != 0:
                    neighbor_dist = distance[k]
                    neighbor = k
            data = np.vstack((data,yi[0][neighbor]))
            print(yi[0][neighbor])

U0 of hyrogen: -13.61 eV
U0 of carbon: -1029.86 eV
U0 of oxygen: -2042.61 eV
U0 of oxygen: -1485.30 eV
None
0
C -2.8340169e-06 2.3049886e-06 -1.4378233e-07
H 0.014845718 -1.0918331 -0.0060250196
H 1.0244261 0.3779494 -0.007724565
H -0.52811974 0.36172476 -0.88464487
H -0.5111183 0.3521308 0.89839613

[-1033.4418]
[-1033.4418]
[-1033.4418]
[-1033.4418]
1
N -0.03160822 0.021159047 0.060332563
H 0.026075294 -0.9904034 -0.029608395
H 0.9246072 0.35579658 -0.030988995
H -0.5114599 0.34058344 -0.77777386

[-1488.8762]
[-1488.8762]
[-1488.8762]
2
O -0.056248687 0.035458494 0.0007260183
H 0.042878296 -0.9215089 -0.00534094
H 0.84990215 0.35871136 -0.0061824406

[-2046.1559]
[-2046.1559]
3
C 0.5995395 0.0 0.0
C -0.5995395 0.0 0.0
H -1.6616386 0.0 0.0
H 1.6616386 0.0 0.0

[-1034.5044]
[-1034.5044]
4
C -0.0075630867 0.5570853 0.003070365
N 0.008071566 -0.59453905 -0.0032767907
H -0.022041854 1.6235689 0.008948269

[-1034.7145]
5
C -0.008137181 0.5992856 0.002790173
O 0.0081545 -0.60058945 -0.0028

[-1033.7496]
[-1033.7496]
[-1033.7496]
[-1033.9045]
[-1033.9045]
[-1033.9045]
[-1033.9045]
[-1033.7496]
[-1033.7496]
[-1033.7496]
39
C 0.74676186 1.8234588 0.0026987367
C 0.71465826 0.29370835 -0.0053245095
C -0.7016382 -0.2650462 0.0052626343
O -0.61744595 -1.6824552 -0.003045157
H 1.7753277 2.1956031 -0.005183291
H 0.23768522 2.239137 -0.8741201
H 0.25471118 2.2295043 0.893636
H 1.2319598 -0.093814634 -0.8907419
H 1.2488378 -0.10337167 0.86572224
H -1.2367903 0.09749595 0.8990794
H -1.253763 0.106896155 -0.8742458
H -1.5111663 -2.0367522 0.0027662576

[-1033.7562]
[-1033.7562]
[-1033.7562]
[-1033.8988]
[-1033.8988]
[-1033.7383]
[-1033.7383]
[-2046.6508]
40
C -0.37670365 1.7365772 -0.58901405
C -0.35834232 0.21751666 -0.60221523
O 0.32608134 -0.23554656 0.54658806
C 0.3953768 -1.6371869 0.623925
H 0.6429466 2.1321328 -0.59214145
H -0.9014168 2.1197355 -1.4693707
H -0.8841458 2.1059532 0.30665258
H -1.3875031 -0.18209246 -0.6149588
H 0.13942331 -0.15579951 -1.5142956
H -0.6056665 -2.09

[-1033.8163]
[-1033.8163]
[-1033.8163]
[-1033.9797]
[-2046.7494]
[-1034.7041]
67
C -0.11099364 1.4434184 0.47809538
N -0.002798127 -0.002016144 0.43176952
C 0.040001623 -0.7200755 1.6851245
C 0.0540585 -0.6464266 -0.76813227
O 0.023135666 -0.11581948 -1.8586168
H 0.74327797 1.8817167 1.0089498
H -0.12971443 1.8105667 -0.5480162
H -1.0296397 1.7494612 0.99398965
H -0.86776423 -0.5423311 2.2763772
H 0.11974856 -1.7927177 1.4909891
H 0.90314484 -0.4131328 2.290089
H 0.13439374 -1.7437677 -0.63557583

[-1033.6616]
[-1033.6616]
[-1033.6616]
[-1033.62]
[-1033.62]
[-1033.62]
[-1035.0364]
68
C 0.018523093 1.929746 0.379988
C -0.019834245 0.42132896 0.32397303
O -0.13818796 -0.2750277 1.3099643
C 0.09629224 -0.24921714 -1.0405195
O 0.044388887 -1.6388092 -0.9297619
H 0.95624065 2.3015738 -0.047489148
H -0.7948941 2.3523576 -0.2200705
H -0.07350858 2.267425 1.4126698
H -0.7145395 0.13458408 -1.6828277
H 1.0387402 0.083044395 -1.5081964
H -0.05502138 -1.807575 0.021652836

[-1033.8749]
[-1033.874

H -1.6806134 0.37492883 0.98106444
H 1.6952534 0.4206947 0.9362986
H 1.6686362 0.66370714 -0.8384267

[-1034.0289]
[-1034.0289]
[-1034.0289]
[-1034.0289]
91
C -1.2616206 1.4628454 -0.21782926
C -0.6486883 0.075631395 -0.11350393
C 0.58098555 -0.28217277 -0.99777544
C 1.1679186 -1.0728656 0.20227662
C 0.20731296 -0.2869079 1.1346471
H -0.49945295 2.2392282 -0.082542785
H -1.7277074 1.621726 -1.1971118
H -2.033043 1.6178535 0.5452922
H -1.4267348 -0.68482137 -0.25153473
H 0.40182248 -0.8204018 -1.9322777
H 1.1771164 0.60935706 -1.2210257
H 0.9071746 -2.1342273 0.15422723
H 2.2409737 -0.9899924 0.39049682
H 0.6913425 0.60320425 1.5511265
H -0.27851835 -0.8290169 1.9502268

[-1033.8407]
[-1033.8407]
[-1033.8407]
[-1034.0592]
[-1034.0569]
[-1034.0569]
[-1033.974]
[-1033.974]
[-1034.0569]
[-1034.0569]
92
C -1.111202 1.4803663 0.13194007
C -0.66964763 0.031853613 0.10723244
C 0.086773075 -0.49478114 -1.1347536
C 1.1902907 -0.8637229 -0.12493972
O 0.48532954 -0.21133919 0.9504042
H -0.2959999 

[-1033.9852]
[-2046.6233]
115
C -0.9858387 1.7401342 -1.2759892
C -0.6613332 0.23790275 -1.3683257
C -0.0071309614 -0.28151423 -0.17134842
C 0.53152436 -0.68673986 0.82658917
C 1.1834474 -1.1870353 2.028922
H -0.074068345 2.3258271 -1.1300842
H -1.473905 2.0839558 -2.1930704
H -1.6531878 1.941904 -0.4336209
H -1.586374 -0.32382965 -1.552848
H -0.022546511 0.056375895 -2.2425635
H 0.59694535 -1.9839329 2.4999318
H 2.1753118 -1.5959373 1.8055742
H 1.314915 -0.39228016 2.771866

[-1033.773]
[-1033.773]
[-1033.773]
[-1034.1294]
[-1034.1294]
[-1033.9126]
[-1033.9126]
[-1033.9126]
116
C 0.94684124 2.0956783 -0.17391336
O 0.98699117 0.70980453 0.13944153
C -0.16463257 0.03637097 -0.05687711
N -0.23924996 -1.1940645 0.18839501
C -1.5100542 -1.8446642 -0.048320945
H 1.9424177 2.4876478 0.03744484
H 0.7138638 2.263366 -1.232763
H 0.21404307 2.6282375 0.44491547
H -0.99471545 0.6538453 -0.4381225
H -1.8693906 -2.30031 0.88157195
H -2.296394 -1.1714119 -0.42865878
H -1.3780218 -2.6592774 -0.769712

...

[-1033.9817]
[-1033.9817]
[-1033.9817]
[-1035.063]
[-1490.0717]
[-2046.9926]
[-2047.0388]
4939
C -0.045806523 2.5430954 -0.56058145
C -0.0043380978 1.0475192 -0.5322453
C 0.07064663 0.20163389 -1.5902216
O 0.08795937 -1.0954679 -1.1770958
C 0.02191466 -1.0822467 0.18772064
C 0.027816363 -2.4118178 0.8541924
C -0.036688875 0.20243092 0.6416086
C -0.118249685 0.67880726 2.0588095
H 0.7972842 2.9823217 -0.013730962
H -0.0077959793 2.9201338 -1.5864244
H -0.96073025 2.9318974 -0.097421095
H 0.11737972 0.35684243 -2.6561253
H -0.82302815 -3.0250382 0.53508127
H 0.93956685 -2.9742298 0.62128246
H -0.028492367 -2.2937648 1.938335
H 0.7347407 1.3168762 2.3202984
H -1.0231867 1.2734358 2.2335672
H -0.13250741 -0.15478991 2.7659605

[-1033.9918]
[-1033.9918]
[-1033.9918]
[-1035.1567]
[-1033.9569]
[-1033.9569]
[-1033.9569]
[-1034.0012]
[-1034.0012]
[-1034.0012]
4940
C -0.033685956 2.540921 -0.55433065
C -0.02951043 1.0456183 -0.5395771
C -0.121567525 0.19125931 -1.5914631
O -0.10040422 -1.1014531

[-1489.3765]
[-1489.3765]
[-1034.8555]
[-1489.3065]
[-1489.3065]
[-1489.3981]
[-1489.3981]
4952
N -0.50736445 2.4384124 -0.04469135
C -0.56485236 1.0409074 0.013946062
C -1.6282572 0.19446565 0.03722324
O -1.1802174 -1.1212416 0.0153079685
C 0.16549139 -1.0865934 -0.009895774
N 0.8347451 -2.3011343 -0.08728332
C 0.6060055 0.20285119 -0.016398812
O 1.9175968 0.6247178 0.041532446
H 0.30264673 2.7919343 0.451095
H -1.3422465 2.8875062 0.30815014
H -2.6954613 0.32286963 0.05717287
H 0.43331692 -3.004709 0.5220947
H 1.817925 -2.1788776 0.12166224
H 2.1703622 0.96460414 -0.8248483

[-1489.3912]
[-1489.3912]
[-1034.8005]
[-1489.3386]
[-1489.3386]
[-2047.0933]
4953
N -0.55647326 2.425214 0.056640334
C -0.58447146 1.0314916 0.010480539
C -1.6309364 0.16364375 0.017057905
O -1.1440018 -1.1442558 0.013166632
C 0.1963545 -1.0546945 0.016539155
O 0.8990015 -2.2036042 -0.0039719595
C 0.62323856 0.23626551 0.007863722
N 1.9312607 0.7818939 -0.07344392
H 0.30737844 2.7756596 -0.34205967
H -1.3547633 

[-1033.6772]
[-1033.6772]
[-1033.6772]
[-1489.2534]
[-1489.2534]
[-1034.9016]
[-1034.9727]
[-2046.9795]
4966
C -0.11921527 2.0266328 0.0037742609
N -0.02701298 0.58187133 -0.013229406
C -0.031995453 -0.2563083 -1.1403053
N -0.17675272 0.30363747 -2.425354
C 0.054784708 -1.5258303 -0.64336157
N 0.11450939 -1.5143852 0.7420298
C 0.07097984 -0.24764284 1.0541996
O 0.11509006 0.27556074 2.2956977
H 0.8534989 2.489733 0.20250407
H -0.47561762 2.3492172 -0.9754958
H -0.82046723 2.34687 0.7777417
H 0.7073856 0.40047333 -2.9153101
H -0.7932823 -0.25367114 -3.003658
H 0.071772724 -2.4521148 -1.1975902
H 0.17349708 -0.47793433 2.8965838

[-1033.6925]
[-1033.6925]
[-1033.6925]
[-1489.2758]
[-1489.2758]
[-1034.7758]
[-2046.9259]
4967
C -0.04833676 1.9926168 0.010894956
N -0.02645909 0.5447199 0.0030828023
C 0.001851707 -0.26321888 -1.1136961
O -0.01845165 0.36357045 -2.3235757
C 0.0452713 -1.5736922 -0.7296147
C 0.052250423 -1.581515 0.7120109
C 0.012846655 -0.2752939 1.1107311
O 0.004777163 0.338

[-1033.6935]
[-1033.6935]
[-1033.6935]
[-1035.1857]
[-1033.919]
[-1033.919]
[-1033.919]
[-2047.0344]
4980
C 0.03859307 2.4286773 -0.5383178
N 0.012040612 0.9838593 -0.5104859
C -0.033269893 0.15601395 -1.5869082
N -0.040601194 -1.1141276 -1.2410511
C -0.0081220865 -1.1102307 0.13041767
N -0.058247745 -2.3113768 0.86060137
C 0.015057812 0.17561977 0.62348086
C 0.021572836 0.69801164 2.0183492
H 0.9412356 2.8181577 -0.05563519
H 0.029962618 2.7617517 -1.5779989
H -0.8349866 2.8526847 -0.031748153
H -0.0562259 0.53740627 -2.5974119
H -0.031632435 -3.0921192 0.21526054
H 0.71059626 -2.4054031 1.5136454
H 0.9823584 1.1407874 2.315517
H -0.7493762 1.4614505 2.1823096
H -0.18878576 -0.12512149 2.7066555

[-1033.6633]
[-1033.6633]
[-1033.6633]
[-1035.173]
[-1489.3033]
[-1489.3033]
[-1033.9226]
[-1033.9226]
[-1033.9226]
4981
C -0.017829055 2.424629 -0.55129683
N -0.06723323 0.9781352 -0.53296965
C -0.30267733 0.12304113 -1.5877236
N -0.2786596 -1.1352204 -1.225067
C -0.015941992 -1.122348 0.130

[-1034.3862]
[-1034.3862]
[-1035.0674]
[-1035.0607]
[-1490.0963]
4995
N -1.5785382 -2.7026637 0.4254778
C -1.561861 -1.5727046 0.18846478
C -1.5439094 -0.13552052 -0.10984901
C -0.16707522 0.43198937 -0.20794034
C 0.56195813 0.9928872 -1.2020725
N 1.8040813 1.3688298 -0.70549226
C 1.7629083 1.0198511 0.53712624
O 0.600462 0.4449106 0.9256026
H -2.0600986 0.03344279 -1.0600187
H -2.12204 0.3838622 0.6644893
H 0.28819245 1.1527575 -2.2329435
H 2.5250974 1.1271173 1.2925936

[-1034.4464]
[-1034.4464]
[-1035.0358]
[-1035.0956]
4996
N -2.061269 -1.8829396 -1.332708
C -1.7324541 -1.2837163 -0.4011052
C -1.2628479 -0.5054199 0.74272144
C 0.031392872 0.20931296 0.45508006
N 0.6650061 0.9739019 1.3134414
C 1.7840326 1.4185709 0.6466793
C 1.819622 0.913593 -0.62566054
N 0.6871769 0.13743298 -0.73697215
H -2.0354447 0.21944003 1.0238616
H -1.13764 -1.1731125 1.6028705
H 2.4963863 2.0750391 1.1220407
H 2.51592 1.0245668 -1.4395766
H 0.39112264 -0.38848847 -1.5442554

[-1034.313]
[-1034.313]
[-1034

In [5]:
print('DONE')  
savetxt('../../../../data/data.csv',data,delimiter=',')
savetxt('../../../data/dataO.csv',datao,delimiter=',')
savetxt('../../../data/dataH.csv',datah,delimiter=',')
savetxt('../../../data/hae.csv',datahae,delimiter=',')
savetxt('../../../data/oae.csv',dataoae,delimiter=',')


DONE


FileNotFoundError: [Errno 2] No such file or directory: '../../../data/dataO.csv'